Ce Mineur construit les tournées  des artistes à partir d'une première sélection.
SI cette tournée est supérieure à 5000 km, l'artiste est pris en compte pour l'étude d'optimisation des tournées. 



In [6]:
import geopy
import pickle
import json
import pymongo
from geopy.distance import vincenty
#import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
from slugify import slugify
import math
from numbers import Number

# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["bandsintown"]

# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'
#retrieve trip coords for each artist
dict_coords={}

import numpy as np
from matplotlib import pyplot as plt
DELTA_BETWEEN_DATES = 15,
MIN_DELTA_BETWEEN_DATES =4,
PLANE_DISTANCE = 1500,
MINIMUM_DATES = 5;

col = db[ 'selectedArtists' ]
newcol = db[ 'minedArtists' ];


In [7]:
from collections import defaultdict, OrderedDict
from operator import getitem 
from geopy.distance import geodesic
from datetime import timedelta
import math







artistList = [];
    
for artist in    col.find( {} ):
    artistList.append(artist["_id"])
    #print len(artist["gigs"]) 
    if len(artist["gigs"])<= MINIMUM_DATES:
        pass
    else:
        print "~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~"
        print artist["_id"]
        
        DICT_GIGS={}
        ARRAY_GIGS_DATETIME=[]
    
        #print artist["gigs"]
        for gig   in artist["gigs"]:
            DICT_GIGS[gig["datetime"]] = gig
            ARRAY_GIGS_DATETIME.append(gig["datetime"])
        #print "________"
    #print ARRAY_GIGS
        
        ORDERED_DICT_OF_GIGS = OrderedDict(sorted(DICT_GIGS.items(), 
           key = lambda x: getitem(x[1], 'datetime'))) 
        #print artist["_id"]
        #print ORDERED_DICT_OF_GIGS 
        totalKm = 0
        timeOnTour = 0;
        timeOffTour = 0;

        tours = [];
        tour = {};
        tour["gigs"] = [];

        singleGigs = [];
        toursCoords = {};
        idTour =0;
        tour["tourCoords"] =[];
        tourInProgress = False;
        dupl =0
        #print ARRAY_GIGS_DATETIME
        
        sorteddates = sorted(ARRAY_GIGS_DATETIME)
        #print sorteddates[0]
        #print sorteddates[1]
        #for (i= 0;i<=len(sorteddates-1),i++):
        i=0
        while(i<=(len( sorteddates)-2)): 
        
            
            #print index
            #print i
            #print sorteddates[i]
            #print sorteddates[i+1]
            GIG= ORDERED_DICT_OF_GIGS.get(sorteddates[i])
            NEXTGIG=ORDERED_DICT_OF_GIGS.get(sorteddates[i+1])
            #print GIG
            #print ORDERED_DICT_OF_GIGS.get(sorteddates[i+1])
            km=geodesic((GIG["venue"]['latitude'],GIG["venue"]['longitude']),(NEXTGIG["venue"]['latitude'],NEXTGIG["venue"]['longitude'])).km 
            #print km
            #nextgig=ORDERED_DICT_OF_GIGS[index]
            
            totalKm+=km
            #print totalKm
            GIG["distanceToNextGig"]= km
            GIG["timeToNextGig"]=(NEXTGIG["datetime"]-GIG["datetime"]).total_seconds()
            #print GIG["timeToNextGig"].total_seconds()
            #print timedelta(hours=4).total_seconds()
            #print str(GIG["timeToNextGig"].seconds),'TTNGG'
            #print "DELTA",timedelta(hours=4)
            #cd=timedelta(hours=4)
            #print cd
            if GIG["timeToNextGig"]<= timedelta(hours=4).total_seconds():
                dupl+=1
                
                pass
                
            
            
            elif (GIG["timeToNextGig"]> timedelta(hours=4).total_seconds())  and ( GIG["timeToNextGig"]<= timedelta(days=15).total_seconds()):
            #on tour
                if tourInProgress == False:
                  #  print "TOUR START"
                    tour={}
                    tour["gigs"]=[]
                    tour["tourCoords"]=[]
                
              #  print "TOUR CONTINUE 2"
                tour["gigs"].append(GIG)
                #print tour["gigs"]
                tourInProgress = True
                #print  tourInProgress
                #print GIG["timeToNextGig"]
                timeOnTour += GIG["timeToNextGig"]/3600
                tour["tourCoords"].append ([(GIG["venue"]['latitude'],GIG["venue"]['longitude'])])
            else:
                if tourInProgress == False:
                    singleGigs.append( GIG );
                 #   print "SG GIG"
                    tourInProgress = False
                else:
                   # print "TOUR END"
           
                    tour["distance"] = 0;
                    for g in tour["gigs"]:
                        tour['distance'] += g["distanceToNextGig"];
                    
                    tour["gigs"].append(GIG)
                    tour["tourCoords"].append ([(GIG["venue"]['latitude'],GIG["venue"]['longitude'])])
                    tour["nbGigs"] = len(tour["gigs"])
                    tourInProgress = False;
           #         print "TOUR"

                    tours.append( tour );
                timeOffTour += GIG["timeToNextGig"]/3600
            if ( i == len(sorteddates) - 2 ) :
                    #    print "HERE"
                        if tourInProgress==True:
                     #       print 'HERE2'
                            #print tour
                            tour["distance"] = 0;
                            for d in tour["gigs"] :
                                tour["distance"]  += d["distanceToNextGig"]
                            

                            tour["gigs"].append(NEXTGIG)
                            tour["nbGigs"] = len(tour["gigs"])
                            tour["tourCoords"].append ([(NEXTGIG["venue"]['latitude'],NEXTGIG["venue"]['longitude'])])
                            tourInProgress = False;
         #                   print "TOUR"
                            tours.append( tour )
                        else : 
                            singleGigs.append( NEXTGIG );
                            tourInProgress = False;
                            
            i+=1  
            
        nbDatesOnTour = 0
        #print "TOURS",tours
        
        for tour in tours:
            nbDatesOnTour += len(tour["gigs"])
            
            
        
            
        #print "TOUR",tour   
        #print len(tours)
        if len(tours) >1:
            
            meanTourLength = nbDatesOnTour / len(tours)
        #print "MEAN TOUR LENGTH",meanTourLength

             #    //ecart type
            sqEcarts = [];
            sumSqEcarts = 0;
            for toursq in tours:
                sqEcart= (len(toursq["gigs"]) - meanTourLength)**2
                sqEcarts.append(sqEcart)
                sumSqEcarts+=sqEcart

            ecartType = math.sqrt( sumSqEcarts / len(sqEcarts) );

#                // calculate total time
                
        totalTime = (ARRAY_GIGS_DATETIME[-1]-ARRAY_GIGS_DATETIME[0]).total_seconds()/3600

               #//TOUR DUTY CYCLE
        tourDutyCycle = timeOnTour / (totalTime);
            #    // console.log('tourDutyCycle = timeOnTour / totalTime:', tourDutyCycle * 100, '%' );

            #    // calcul du nombre moyen de dates / année
        meanOfGigsPerYear = len(artist["gigs"]) / (totalTime)
            #    // console.log('meanOfGigsByYear:', meanOfGigsPerYear);

            #   // calcul du délais moyen entre 2 concerts
        meanDelayBetweenGigs =(totalTime/24) / len(artist["gigs"])
     #           // console.log('meanDelayBetweenGigs:', meanDelayBetweenGigs, "days");

      #          //source: http://www.sightline.org/research/graphics/climate-co2bymode/
        co2Spent = totalKm / 3;
                #// console.log('co2 depense par membre du groupe (en kg) /premiere approx:', co2Spent);
        artist["name"] = artist["_id"]
        artist["slug"] = slugify( artist["_id"] )
        del  artist["_id"]  #remove id to allow auto mongo id
        artist["tours"] = tours
        artist["singleGigs"] = singleGigs
        artist["totalKm"] = totalKm
        artist["totalGigs"] = nbDatesOnTour + len(singleGigs)
        if len(tours) >1:
            artist["ecartType"] = ecartType
            
        artist["tourDutyCycle"] = tourDutyCycle
        artist["meanOfGigsPerYear"] = meanOfGigsPerYear
        artist["meanDelayBetweenGigs"] = meanDelayBetweenGigs
        artist["co2Spent"] = co2Spent
        #print "artist", artist
        
        
        if artist["totalKm"] > 5000:
            print "PUSHING ARTIST ",artist["name"]
            print len(artist["gigs"])
            newcol.insert(artist)

print artistList[:20]

~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Adestria, Erra
PUSHING ARTIST   Adestria, Erra
13
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Joey Cape, Jon Snodgrass & Brian Wahlstrom
PUSHING ARTIST   Joey Cape, Jon Snodgrass & Brian Wahlstrom
14


/home/goonieb/gitrep/bandstour/venv/lib/python2.7/site-packages/ipykernel_launcher.py:214: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.


~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Novustory
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Phil Campbell and the Bastard Sons
PUSHING ARTIST   Phil Campbell and the Bastard Sons
42
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
!!!
PUSHING ARTIST  !!!
386
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
"Acoustic Africa"
PUSHING ARTIST  "Acoustic Africa"
25
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
"Scream The Prayer"
PUSHING ARTIST  "Scream The Prayer"
14
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
"Super DJ" Romeo
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#1 Dads
PUSHING ARTIST  #1 Dads
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#PushYourDrumming/RolandVDrums
PUSHING ARTIST  #PushYourDrumming/RolandVDrums
17
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
$uicideboy$
PUSHING ARTIST  $uicideboy$
23
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
$wingin' Utter$
PUSHING ARTIST  $wingin' Utter$
37
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

PUSHING ARTIST  257ers
113
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
25th anniversary tour
PUSHING ARTIST  25th anniversary tour
12
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
27 Club
PUSHING ARTIST  27 Club
23
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
28 Degrees Taurus
PUSHING ARTIST  28 Degrees Taurus
28
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
28 Double
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
28DAYS
PUSHING ARTIST  28DAYS
176
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
29TH STREET SWINGTET
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2BAL
PUSHING ARTIST  2BAL
20
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2Bangers
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2Cellos
PUSHING ARTIST  2Cellos
215
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2Elements Fanpage
PUSHING ARTIST  2Elements Fanpage
153
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2Empress
PUSHING ARTIST  2Empress
105
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

PUSHING ARTIST  6 String Drag
37
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
6'10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
60
PUSHING ARTIST  60
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
609
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
64 To Grayson
PUSHING ARTIST  64 To Grayson
192
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
65 Shapeshifters
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
65daysofstatic
PUSHING ARTIST  65daysofstatic
424
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
68
PUSHING ARTIST  68
454
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
69db
PUSHING ARTIST  69db
71
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
6LACK
PUSHING ARTIST  6LACK
44
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
7 Come 11
PUSHING ARTIST  7 Come 11
12
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
7 Dials Mystery
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
7 Horns 7 Eyes
PUSHING ARTIST  7 Horns 7 Eyes
19
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

...

PUSHING ARTIST  rødhåd
266
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
s.o.
PUSHING ARTIST  s.o.
58
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
sHEPARD
PUSHING ARTIST  sHEPARD
62
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
sab
PUSHING ARTIST  sab
18
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
sabb
PUSHING ARTIST  sabb
39
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
salvation AMP
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
sandy Campbell, Robby Campbell, steve Volk, Steven Gore , Mario Bozza,anthony albanese
PUSHING ARTIST  sandy Campbell, Robby Campbell, steve Volk, Steven Gore , Mario Bozza,anthony albanese
27
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
sasasas
PUSHING ARTIST  sasasas
20
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
schlachthofbronx
PUSHING ARTIST  schlachthofbronx
89
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
schoolboy
PUSHING ARTIST  schoolboy
7
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
scott elkins
~~~~~~~~~~~~~~~~~

PUSHING ARTIST  the Candles
88
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Central Plains
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Classic Rock Show
PUSHING ARTIST  the Classic Rock Show
136
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Closers
PUSHING ARTIST  the Closers
12
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Coldies
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Collingwood
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Colorines
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Colourist
PUSHING ARTIST  the Colourist
10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Commonwealth
PUSHING ARTIST  the Commonwealth
62
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Coral Reefer Band
PUSHING ARTIST  the Coral Reefer Band
117
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Cordovas
PUSHING ARTIST  the Cordovas
219
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Courtesans
PUSHING ARTIST  the Courtesans
41
~~~

~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Roe Family Singers
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Roof
PUSHING ARTIST  the Roof
19
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Rough
PUSHING ARTIST  the Rough
21
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Ruination
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Run Around
PUSHING ARTIST  the Run Around
28
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the SPiKEDRiVERs
PUSHING ARTIST  the SPiKEDRiVERs
81
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Schooley Mountain Band
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Scotch Bonnets
PUSHING ARTIST  the Scotch Bonnets
86
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shady Horns
PUSHING ARTIST  the Shady Horns
49
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shag Rats
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shills
PUSHING ARTIST  the Shills
65
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shi

PUSHING ARTIST  wankelmut
190
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wavelengths
PUSHING ARTIST  wavelengths
13
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wax wings
PUSHING ARTIST  wax wings
10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
waxworks
PUSHING ARTIST  waxworks
21
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wayne's world
PUSHING ARTIST  wayne's world
13
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
we dream dawn
PUSHING ARTIST  we dream dawn
31
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
weRcalled
PUSHING ARTIST  weRcalled
53
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
weiherer
PUSHING ARTIST  weiherer
52
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wellRED Comedy Tour
PUSHING ARTIST  wellRED Comedy Tour
46
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wellman
PUSHING ARTIST  wellman
16
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wellwell
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wes finch music
~~~~~~~~~~~~~~~~~~~~~~~

PUSHING ARTIST  鼓童
76
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
비
PUSHING ARTIST  비
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
조수미
PUSHING ARTIST  조수미
10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
Nick Cave
PUSHING ARTIST  Nick Cave
431
[u'       Amy Kaiser, director', u'       Kevin McBeth, director', u'    Carnovoure Breat', u'   WaveRadio', u'  Blackened (Metallica Tribute)     ', u' (Goutte de Terre Outdoor)', u' (feat. ex-Jaded Heart-Frontman Michael Bormann and Dario Velasco on vocals)', u' *** Pacman (S.U.B/Shockwave303)***', u' 4 Warned', u' @CJ_IDJ', u' @MckNastyMusic', u' AND STILL I CHASE THE SUN', u' Adam Zelkind ', u' Adestria, Erra', u' Alabaster De Plume', u' Alex Arnout', u' Alexis Raphael', u' Alyssa & Melissa', u' Appomattox Rebellion', u' Arkhon']


In [8]:
for band in db.minedArtists.find() :
        print band["name"]

 Adestria, Erra
 Joey Cape, Jon Snodgrass & Brian Wahlstrom
 Phil Campbell and the Bastard Sons
!!!
"Acoustic Africa"
"Scream The Prayer"
#1 Dads
#PushYourDrumming/RolandVDrums
$uicideboy$
$wingin' Utter$
& The Shudderbugs
'77
'Stache!
'Thee' Duke of Dark
(de)absolve
(həd) p.e.
...And You Will Know Us by the Trail of Dead
.38 Special
070 SHAKE
070shake
0phe1ia
1 Last Chance
1-800 DINOSAUR
10 String Symphony
10 Years
10,000 Maniacs
100 Proof
1000 Miles of Fire
1000Mods
1001
10cc
112
11th Hour
12
12 Stones
12th Planet
13 Scars
1349
138
14
15
16
1605
16BIT
17
17 Hippies
1776
182 - UK Tribute Act To Blink 182
187 Strassenbande
18th & Addison
1910 Fruitgum Company
1939 Ensemble
1977
1988
19th Street Band
1Lady
2 Bad Mice
2 CELLOS
2 Chainz
2 Elements
2 IN THE CHEST
2 Many DJ's
2 Mile Final
20 Watt Tombstone
21
21 Savage
219 Boys
22
222
23
24 HORAS
24HRS
257ers
25th anniversary tour
27 Club
28 Degrees Taurus
28DAYS
2BAL
2Cellos
2Elements Fanpage
2Empress
2Steel Girls
2Tone
2X4
2b2
2nd Room
2r

After the Fall
After the Flood
AfterShow
Afterhours
Aftermath
Afternoon Delight
Afternoon Tea
Afterparty
Aftershock
Afu-Ra
Again
Against All Odds
Against Himself
Against Me!
Against The Current
Against The Grain 
Against the Plagues
Agar Agar
Age of Days
Age of Woe
Agent
Agent Fresco
Agent Orange
Agents Of Time
Ages And Ages
Ages Apart
Agnes Milewski
Agnes Obel
Agnieszka Chylińska
Agnostic Front
Agony
Agoraphobic Nosebleed
Agori Tribe
Agoria
Ags Connolly
Ah
Ahab
Ahleuchatistas
Ahmad Jamal
Ahmed Ahmed
Ahmed Sylla
Ahn Trio
AiNA ROXX
Aida
Aida Rodriguez 
Aidan Connell
Aidan Doherty
Aiden
Aiden Jude
Ailie Robertson
Aim
Aimee Mann
Aiming For Average
Aiming for Enrike
Ain't Misbehavin'
Aine O'Doherty
Air Credits
Air Drawn Dagger
Air Dubai
Air For Ants
Air Supply
Air Traffic
Air Traffic Controller
Air Waves
Air Zaïre
Airbourne
Aircraft
Airdice
Aireene Espiritu
Airelle Besson
Airi
Airling
Airpark
Airplane Mode
Airside
Airwave
Airways
Aisha Burns
Aisha Devi
Aisles
Aisling Iris
Aitas
Aja
Aja Gam

Amy Andrews
Amy Becker
Amy Benton
Amy Cook
Amy Estrada
Amy Fairchild
Amy Gerhartz
Amy Grant
Amy Helm
Amy LaVere
Amy Leon
Amy Lynn & The Honey Men
Amy Macdonald
Amy Miller
Amy Obenski
Amy Petty
Amy Ray
Amy Sailor Band
Amy Schumer
Amy Shark
Amy Speace
Amy Stroup
Amy Unland
Amy Vachal
Amygdala
Amyst
Amythyst Kiah
An Albatross
An American In Paris
An Appalachian Christmas
An Eagle In Your Mind
An Early Cascade
An Evening with Bruce Hornsby (solo)
An Honest Year
An Irish Christmas
An Pierlé
An-ten-nae
AnGy KoRe
Ana Cristina
Ana Moura
Ana Popovic
Ana Torroja
Anaal Nathrakh
Anabelle Kay
Anahata
Anais Mitchell
Analog Son
Anane Vega
Anarbor
Anastacia
Anastasia
Anat Cohen
Anat Cohen Quartet
Anat Fort
Anatevka
Anathema 
Anatomy
Anaïs
Anaïs Delva
Anberlin
Anchor
Anchored
Anchors
Anchorsong
Ancient Astronauts
Ancient Cities
Ancient Methods
Ancient Ocean
Ancient Sun
Ancient Vvisdom
Ancients
And So I Watch You From Afar
And The Kids
And.ID
Andalyn
Andead
Anders
Anders Osborne
Anders Parker
Anderson
A

Avion Roe
Avishai Cohen
Aviva Jaye
Avon Dale
Avíon Blackman
Awa Ly
Await Rescue
Awake at last
Awaken
Awaken the Empire
Awe
Aweminus
Awesome Tapes From Africa
Awir Leon
AxH
Axe Murder Boyz
Axel Bauer
Axel Boman
Axel Prahl
Axel Ritt
Axel Rudi Pell
Axel Zwingenberger
Axes
Axis
Axis:Sova
Axwell
Aya
Aycee Lovely
Ayiesha Woods
Ayla Brown
Ayla Nereo
Aymeric MAINI
Aynsley Lister
Ayo
Ayo Jay
Ayreheart
Azad
Azar Lawrence
Aziz
Azizi Gibson
Aztec
Aztec Two-Step
Aztek
Azucar
Azul
Azure
Azymuth
Aérea Negrot
B Boys
B L A C K I E
B and The Hive
B*Witched
B-Fade Music
B-Free
B-Linda
B-Liv (DJ & Producer)
B-Man & the Mizzbeehavens
B-SHOC
B-Side
B-Side Players
B-Style
B-Sydes
B-Tight
B. B. & The Blues Shacks (D)
B. Dolan
B.B. King 
B.J. Thomas
B.M.C. Big Mountain County
B.O.B
B.R. Lively
B.T.
B.Traits
BABYLON
BABYMETAL
BACK TO THE 90S
BACK TO THE EIGHTIES SHOW
BACK:N:BLACK
BACKPACKS
BACTEREMIA
BAD
BAD BREEDING
BAD LUCK
BAD MULES
BADBADNOTGOOD
BAET
BAK XIII
BANDA S7
BANDITS
BARK .Loud
BASKERY
BAST
BAT
BAT

Big D and the Kids Table
Big Daddy Kane
Big Daddy Love
Big Daddy Weave
Big Daddy Wilson
Big Data
Big Dope P
Big Drill Car
Big E
Big Eater
Big Eyes
Big Fat Shakin
Big Frank
Big Freedia
Big Gigantic
Big Ginger Kid
Big Gus and Swampadelic
Big Harvest
Big Head Todd and The Monsters
Big Hix
Big Hoss
Big Infinite
Big James And The Chicago Playboys
Big Jay Oakerson
Big Jesus
Big Joe Walker
Big John Bates
Big K.R.I.T.
Big Kettle Drum
Big Kitty
Big Lenbo
Big Lo
Big Mama Shakes
Big Mean Sound Machine
Big Mo
Big Moon
Big Mountain
Big One
Big Red
Big River
Big Sam's Funky Nation
Big Sandy
Big Sean
Big Search
Big Sexy
Big Shot
Big Sleep
Big Story
Big Sugar
Big Thief
Big Tim Kellams
Big Time Grain Co.
Big Top
Big Trouble
Big Ups
Big Water
Big Wig
Big Wild
Big Words
Big Worm
Big Wreck
Big in Japan
BigJohn Mills
Bigflo & Oli
Bigfoot 
Bigfoot Buffalo
Bigwig
Bijou
Bike
Bilderbuch
Bile
Bill
Bill Anderson
Bill Bailey
Bill Bellamy
Bill Burr
Bill Callahan
Bill Carter and the Blame Fan Page
Bill Charlap
Bill

...

The Twinkle Brothers
The Two Tens
The Two Tracks
The Ty Curtis Band
The Tyde
The Tymes
The U.N.
The Ugly
The Ugly Beats
The Ugly's
The Ukeladies
The Ukulele Orchestra Of Great Britain
The Undead
The Underachievers
The Undercover Dream Lovers
The Undercover Hippy
The Underground
The Underground Railroad to Candyland
The Undertakers
The Undertones
The Unit
The Universal Thump
The Unlikely Candidates
The Unseen
The Untouchables
The Upbeats
The Upper Crust
The Upper Strata
The Uppercuts
The Uprising
The Urban Cowboy Band
The Urban Renewal Project
The Urban Voodoo Machine
The Urge
The Used
The Usual Things
The V.I.P.'s
The Vacant Lots
The Vaccines
The Vagabonds
The Vaginas
The Vagrants
The Vamps
The Van-Dells
The Vandals
The Vanjas
The Vans
The Vapors
The Varukers
The Vaselines
The Veer Union
The Vegabonds
The Veils
The Veldt
The Velvet Teen
The Velveteers
The Velveteins
The Velvets
The Venetia Fair
The Venomous Pinks
The Ventures
The Venus in Furs
The Verdict
The Verve Pipe
The Vespers
The

Timbre
Time Atlas
Time Cat
Time Lock
Time Machine, Dutch Satriani Tribute
Time Sawyer
Time Walk
Time and Distance
Time for T.
Time for Three
Timeflies
Timeless
Timeshares
Timid Boy
Timmy Curran
Timmy Regisford
Timmy T
Timmy The Teeth
Timmy Trumpet
Timmy's Organism
Timo Maas
Timo Räisänen
Timothy
Timothy Eerie
Timothy J. Fairplay
Timothy James
Timothy Reddick
Tin
Tin Men
Tin Pan
TinMan
Tina
Tina Dickow
Tina Guo
Tina Schlieske
Tinariwen
Tinashe
Tinchy Stryder
Tinderbox
Tindersticks
Tine Bruhn
Tinfoil
Tingsek
Tingvall Trio
Tini
Tini Tun
Tinie Tempah
Tink
Tinsley Ellis
Tiny
Tiny Kingdoms
Tiny Moving Parts
Tiny Ruins
Tippa Irie
Tir na nOg
Tire le coyote
Tired Lion
Tiromancino
Tirzah
Tish Hinojosa
Tish Hyman
Titan
Titanic
Titanium Blue
Titans In Time
Titi Robin
Titiyo
Title Fight
Tito & Tarantula
Tito Jackson
Tito Nieves
Tito Puente Jr.
Tito Rojas
Tittsworth
Titus Andronicus
Tituss Burgess
Tiwa Savage
Tiziano Ferro
Tiësto
Tje Austin
Tkay Maidza
Tnertle
To Kill a King
To Rustne Herrer
To Spea

UFO
UK Foo Fighters
UK RAMONES
UK Subs
ULTIMATE POWER
UMA
UME
UMFANG
UN ETE 44
UNKLE
UNNO
UNO Mas
UNSCARRED
UNiiQU3
US Rails
USC Trojans Football
USS [UBIQUITOUS SYNERGY SEEKER]
UUU
UVB
UWE STEIMLE
UZ
UZALA
UZoo
Uada
Ubuntu Music
Uche Agu
Udo Dirkschneider
Udo Lindenberg
Ufer
Uffie
Ufomammut
Ugly
Ugly God
Ugly Kid Joe
Uh Huh Baby Yeah
Uhh Yeah Dude
Ulcerate
Ulf Nilsson
Ulf Wadenbrandt
Uli Jon Roth
Ulla Meinecke
Ulrich Ellison
Ulrich Schnauss
Ulrich Tukur
Ulrika Spacek
Ultimate Bowie
Ultimate Doo Wop Show
Ultimate Eagles
Ultimate Fighting Championship
Ultimate Painting
Ultimate Stones Band
Ultra Naté
Ultra Vomit
Ultrabeat
Ultrafaux
Ultraviolet
Ulvae
Ulver
Ulysse
Ulysses
Ulysses Owens, drums
Uma Galera
Umami
Umberto Maria Giardini
Umberto Tozzi
Umbra
Umek
Ummet Ozcan
Umphrey's McGee
Umwelt
Un
Una Bèstia Incontrolable
Una Walkenhorst
Unabombers
Unaka Prong
Unamused Dave
Unantastbar
Unauthorized Rolling Stones
Unbreakable Hatred
Uncle Bard & The Dirty Bastards
Uncle Chunk
Uncle Dugs
Uncle 

We the Kings
We the People
Weapon
Weapon-X
WeareTreo
Wearing Scars
Weasel Walter
Weathered
Weaver
Webb Wilder
WebsterX
Wedding Banned
Wednesday 13
Wednesdays
Weedeater
Weeding Dub
Weeed
Weekend
Weekend Money
Weekend Pass
Weekender
Ween
Weeping Willows
Weezer
Wehbba
Weihnachten
Weird Is the New Cool
Weird Science
Weirds
Welcome Home
Welcome To Night Vale
Welicoruss
Well Hung Heart
Well Known Strangers
Well$
Well-Strung
Welles
Welshly Arms
Welticke
Wendell Brunious
Wendy DeWitt
Wenn die Musi spielt
Wenzel
Werd2Jah
Werkha
Wes Nickson Band
Wes Swing
Wes Walker
Wesley Michael Hayes
Wesley Stace
Wesley Stromberg
WesliBand
Wess Meets West
West
West Coast Songwriters
West End Blend
West King String Band
West Virginia Mountaineers Football
WestWend
Westafa
Westbam
Western
Western Addiction
Western Caravan
Western Centuries
Western Settings
Westerner
Westfield Massacre
Weston Smith
Westpoint
Westside Andy on Harmonica
Westside Gunn
Wet
Wet Baes
Wet Wet Wet
Wetbrain
Weval
Weyes Blood
Whale Bones


Zion
Zion I Crew
Zion Train
Zipper Club
Zippo
Zissou
Ziv Ravitz
Ziva
Zlabya
Zlata Chochieva
Zo!
Zodiac
Zodiac Mprint
Zoe Lewis
Zoey Dollaz
Zohki
Zola Jesus
Zolle
Zomanno
Zombie Burlesque
Zombie Girl
Zombies in Miami
Zomboy
Zomby
Zona Road
Zonderling
Zoo Roo
Zooey
Zoogma
Zoolander
Zoom
Zorch
Zoso
Zoufris Maracas
Zouk Machine
Zounds
Zoya Naumchik
Zoë Keating
Zoë Nutt
Zoúme
Zu
Zubin Mehta
Zucchero
ZuhG
Zuill Bailey
Zuli
Zulu Wave
ZuluZuluu
Zuse
Zydeco Trouble
Zydepunks
[PIAS] Nites
[STREAKER] Records
[X]-Rx
[dunkelbunt]
[dunkelbunt] DJ Set
[dunkelbunt] LIVE
[spunge]
_ash Aria_
a Boogie
a Giant Dog
a Midsummer Night's Dream
a Step Ahead
a Vision of Elvis
a place both wonderful and strange
a-ha
aTd
aileron
akasha
al mckay
al'tarba
alberto ruiz
alci
alissa.jo
alok
alto clark
aly keita
amatria
ambiq
ami
amine edge
amzy
andreas gabalier
andy montanez
annalisa
anything
apnea
ara
arizona cardinals
arsen
ask:me
athas
auburn tigers football
audio riot
augustines
austin brown
badXchannels
baffa
bal